# Fluid-Structure-interaction

Michael Neunteufel + JS '21

* coupling of non-linear elasticity and Navier-Stokes on moving domain
* strong coupling of velocities via Lagrange parameter
* mesh deformation keeps div-free functions div-free
* Piola transform causes another term like mesh-velocity

In [ ]:
from netgen.geom2d import CSG2d, Circle, Rectangle
from ngsolve import *
from ngsolve.webgui import Draw

tau     = 0.005
tend    = 5.5
order   = 3
alpha   = Parameter(5)
inverse = "umfpack"
truecompile = True

In [ ]:
(rhos, nus, mus, rhof, nuf, U) = (1e4, 0.4, 0.5*1e6, 1e3, 1e-3, 1)
ls = 2*mus*nus/(1-2*nus)

uinflow = CF( (4*U*1.5*y*(0.41-y)/(0.41*0.41), 0) )

def GenerateMesh(order, maxh=0.12, L=2.5, H=0.41):
    r = 0.05
    D = 0.1

    geo = CSG2d()
    circle = Circle( center=(0.2,0.2), radius=0.05, bc="circ" )
    fluid  = Rectangle( pmin=(0,0), pmax=(L,H), mat="fluid", left="inlet", top="wall", bottom="wall", right="outlet" )
    solid  = Rectangle( pmin=(0.248989794855664,0.19), pmax=(0.6,0.21), mat="solid", left="circ_inner", top="interface", bottom="interface", right="interface" )
    
    domain_fluid = (fluid - circle) - solid
    domain_solid = (solid - circle)
    geo.Add(domain_fluid)
    geo.Add(domain_solid)

    # generate mesh
    mesh = Mesh(geo.GenerateMesh(maxh=maxh))
    mesh.Curve(order)
    
    return mesh

mesh = GenerateMesh(order=order)
Draw(mesh)

V1 = VectorH1( mesh, order=order, dirichlet = "wall|outlet|inlet|circ|circ_inner" )
V2 = HDiv( mesh, order=order, dirichlet = "wall|inlet|circ|circ_inner", definedon = "fluid", hodivfree=True )
V3 = TangentialFacetFESpace(mesh, order=order, dirichlet="wall|inlet|circ|circ_inner|outlet", definedon = "fluid" )
V4 = VectorH1( mesh, order=order, dirichlet="circ|circ_inner", definedon = "solid" )
Q  = L2( mesh, order=0, definedon = "fluid", lowest_order_wb=True )
V5 = SurfaceL2( mesh, order=order, dirichlet="wall|outlet|inlet|circ|circ_inner" )

V = V2*V3*Q*V1*V4*V5*V5
Y = V2*V3*Q
H = VectorH1( mesh, order=order, dirichlet = "wall|inlet|outlet|circ|circ_inner" )
              
u, uhat, p, d, v, fx, fy = V.TrialFunction()
ut,uhatt,pt,dt,vt,fxt,fyt = V.TestFunction()
f, ft = CF( (fx,fy) ), CF( (fxt,fyt) )

gfsol     = GridFunction(V) #solution
gfsolold  = GridFunction(V) #oldsolution
gfset     = GridFunction(H) #for SetDeformation
        
gfu, gfvelhat, pressure, gfd, gfv, gffx, gffy = gfsol.components
uold, uhatold, pold, dold, vold, fxold, fyold = gfsolold.components

I = Id(mesh.dim)
F = grad(d) + I
C = F.trans*F
Fold = grad(dold) + I
Cold = Fold.trans*Fold


n,h = specialcf.normal(2),specialcf.mesh_size
        
def tang(vec):
    return vec - (vec*n)*n
def norma(vec):
    return (vec*n)*n

def Stress(mat):
    return mus*mat+ls/2*Trace(mat)*I


#For Stokes problem
stokes = BilinearForm( Y, symmetric = True, check_unused=False )
stokes += (nuf*rhof*InnerProduct( 2*Sym(grad(u)), Sym(grad(ut))) \
           - div(u)*pt - div(ut)*p - 1e-8*p*pt )*dx("fluid")
stokes += (nuf*rhof*(InnerProduct( 2*Sym(grad(u))*n, tang(uhatt-ut) ) \
                     +InnerProduct( 2*Sym(grad(ut))*n, tang(uhat-u) ) \
                     +alpha*order*order/h * InnerProduct( tang(uhatt-ut), tang(uhat-u) ))) \
            *dx("fluid", element_boundary=True)
stokes.Assemble()


######################################### SOLID #############################################
a = BilinearForm(V, symmetric=False, check_unused=False, condense=True)
a += ( (1/tau*(d-dold)-0.5*(v+vold))*dt +rhos/tau*(v-vold)*vt +2*InnerProduct(F*Stress(0.5*(0.5*(C+Cold)-I)), grad(vt)) ).Compile(truecompile,True)*dx("solid")

factor = 1e-22*mus
gfdist = GridFunction(H1(mesh, order=2))
def minCF(a,b) : return IfPos(a-b, b, a)
gfdist.Set( minCF( (x-0.6)**2+(y-0.19)**2, (x-0.6)**2+(y-0.21)**2 ) )
def NeoHookExt (C, mu=1,lam=1):
    return 0.5 * mu * (Trace(C-I) + 2*mu/lam * Det(C)**(-lam/2/mu) - 1)
a += Variation( factor/sqrt(gfdist*gfdist+1e-12)*NeoHookExt(C)*dx("fluid")).Compile(truecompile,True)

################################# FLUID ##############################################
graddp = 1/(tau)*(grad(d)-grad(dold))
relv = u-1/tau*(d-dold)
relvn = relv*n
upwind = (u*n)*n + (IfPos(relvn, tang(u), tang(uhat)))

cfinner = nuf*rhof*InnerProduct(Sym(grad(u))+Sym(grad(uold)),Sym(grad(ut))) - div(u)*pt-div(ut)*p -rhof*InnerProduct(0.5*(u+uold), grad(ut).trans*relv) + rhof*InnerProduct(0.5*graddp*(u+uold),ut) + rhof/tau*(u-uold)*ut
cfouter = nuf*rhof*(InnerProduct(Sym(grad(u)+grad(uold))*n,tang(uhatt-ut)) + InnerProduct(2*Sym(grad(ut))*n,0.5*tang(uhat-u + uhatold-uold)) + alpha*order*order/h*InnerProduct(tang(uhatt-ut),0.5*tang(uhat-u+uhatold-uold)))+rhof*(relvn*upwind*ut+IfPos(relvn,1,0)*0.5*relvn*tang(uhat-u+uhatold-uold)*uhatt)
a += cfinner.Compile(truecompile,True)*dx("fluid",deformation=gfset)
a += cfouter.Compile(truecompile,True)*dx("fluid",element_boundary=True, deformation=gfset)
#interface
a += ((norma(v-u.Trace())+tang(v-uhat.Trace()))*ft + (norma(vt-ut.Trace())+tang(vt-uhatt.Trace()))*f).Compile(truecompile,True)*ds("interface", deformation=gfset)
        

bts = Y.FreeDofs() & ~Y.GetDofs(mesh.Materials("solid"))
bts &= ~Y.GetDofs(mesh.Boundaries("wall|inlet|circ|interface|circ_inner"))
invstoke = stokes.mat.Inverse(bts, inverse = "umfpack")

tmp = GridFunction(Y)
rstokes = tmp.vec.CreateVector()
tmp.components[0].Set( uinflow, definedon=mesh.Boundaries("inlet") )
rstokes.data = stokes.mat*tmp.vec
tmp.vec.data -= invstoke*rstokes
gfsol.components[0].vec.data = tmp.components[0].vec
gfsol.components[1].vec.data = tmp.components[1].vec
gfsol.components[2].vec.data = tmp.components[2].vec

w = gfsol.vec.CreateVector()
res = gfsol.vec.CreateVector()

In [ ]:
gfsol.Load("fsisol4.sol")

scene = Draw(mesh.MaterialCF( {"fluid" :gfu}, default=None), mesh.Materials("fluid"), \
             deformation=gfd, order=3)

t = 3
tend=4
SetNumThreads(4)
with TaskManager():
    while t < tend-tau/2.0:
        t += tau
        print("\rt = ", t, end="")
    
        gfsolold.vec.data = gfsol.vec

        for step in range(3):
            gfset.Set(gfsol.components[3])
            a.AssembleLinearization(gfsol.vec)
            inv = a.mat.Inverse(a.space.FreeDofs(a.condense), inverse=inverse)
            a.Apply (gfsol.vec, res)
            
            if a.condense:
                res.data += a.harmonic_extension_trans * res
            w.data = inv*res
            if a.condense:
                w.data += a.harmonic_extension * w
                w.data += a.inner_solve * res
            err = InnerProduct(w, res)
            # print ("err^2 = ", err)
                                                
            gfsol.vec.data -= w
            
            if abs(err) < 1e-20:
                break;
            
        scene.Redraw()
  
# gfsol.Save("fsisol4.sol")